In [1]:
%load_ext autoreload
%autoreload 2

import numpy as np
from strategy_v2.Strategy import *
from strategy_v2.TradingSubSystem import *
from strategy_v2.Portfolio import *
from strategy_v2.TransactionCost import *
from strategy_v2.Executor import *
from utils.data_helper import *
from utils.data import *
from utils.performance import *
import cvxpy as cp
from plotly.subplots import make_subplots
from croniter import croniter

# Portfolio General Settings
We assume the code is run at T before market open, so it all data on and before T-1 close. Therefore, the end_date should be today - BDay(1)

In [2]:
end_date = get_today()
start_date = pd.to_datetime(datetime(2022, 1, 3))
vol_target = 0.5
max_leverage = 1

# Linear Optimization (Risk-Adjusted Return)

- How to determine the capital?

Difficulty here is portfolio might use different leverage per rebalance, looking at the asset MV might not give you the total portfolio capital (e.g. 70% leverage, your stocks only worth 70% of your capital now)

we can use the market value on Futu divides by the leverage used for last periods. This will give you the total captial for the portfolio

Then we use this capital for next rebalance

We shuold strategically fix this issue by reading capital from Futu or keep track the capital ourselves

- 2024-03-23 - Leverage Ratio = 102.4376
- 2024-04-20 - Leverage Ratio = 102.6119
- 2024-05-03 - Leverage Ratio = 97.8875
- 2024-05-17 - Leverage Ratio = 99.1256
- 2024-05-31 - Leverage Ratio = 102.182
- 2024-06-14 - Leverage Ratio = 101.4418
- 2024-07-20 - Leverage Ratio = 95.64553

In [3]:
156290.69/95.64553*100

163406.1623162107

In [4]:
portfolio = PortfolioLinearOpt(
    capital=163406.1623162107,
    name='ETF Buy and Hold Portfolio',
    lookback_period=60,
    opt_freq=1,
    rebalance_iter=RebalancerIter('0 0 * * Fri', 2),    
    tc_model=TransactionCostFutu(),    
    systems=[
        TradingSubSystemSingle(vol_target=vol_target, instruments=['META'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['TSLA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['NVDA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['AAPL'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['EWY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['DXJ'],   strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),        
        #TradingSubSystemSingle(vol_target=vol_target, instruments=['VOE'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        #TradingSubSystemSingle(vol_target=vol_target, instruments=['VBR'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['BRK-B'], strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['SPY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
        TradingSubSystemSingle(vol_target=vol_target, instruments=['QQQ'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),        
])

portfolio.set_start_date(start_date)
portfolio.set_end_date(end_date)
portfolio.backtest_subsystems()
portfolio.optimize(gamma=10, hhi=0.2)
portfolio.backtest()
portfolio.rebalance()
portfolio.performance(show_all_rets=True)

[*********************100%***********************]  1 of 1 completed

2024-08-10 00:41:25,294 - TradingSubSystemSingle [META] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-08-09......
2024-08-10 00:41:25,305 - TradingSubSystemSingle [META] - INFO - Volatility Target = 50.0% | Price Volatility = 46.6% | Last Scale Factor = 1.05



[*********************100%***********************]  1 of 1 completed

2024-08-10 00:41:25,565 - TradingSubSystemSingle [TSLA] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-08-09......
2024-08-10 00:41:25,574 - TradingSubSystemSingle [TSLA] - INFO - Volatility Target = 50.0% | Price Volatility = 70.6% | Last Scale Factor = 0.69



[*********************100%***********************]  1 of 1 completed

...


[*********************100%***********************]  1 of 1 completed

2024-08-10 00:41:27,246 - TradingSubSystemSingle [QQQ] - INFO - Generating position for strategy BAH1 between 2021-10-04 and 2024-08-09......
2024-08-10 00:41:27,256 - TradingSubSystemSingle [QQQ] - INFO - Volatility Target = 50.0% | Price Volatility = 29.4% | Last Scale Factor = 1.69


100%|██████████| 680/680 [00:03<00:00, 181.85it/s]


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


Rebalanced Portfolio  Optimized Portfolio      ^SPX   
Measure                                                                        
Cumulative Return                    1.765784             1.744500  1.108380  \
Annualized Return                    0.242963             0.238117  0.056007   
Annualized Volatility                0.218684             0.217845  0.180772   
Annualized Sharpe Ratio              0.954786             0.936212  0.120815   
Maximum Drawdown                    -0.263026            -0.272678 -0.254251   

                         Single - META (BAH1)  Single - TSLA (BAH1)   
Measure                                                               
Cumulative Return                    1.616232              0.630929  \
Annualized Return                    0.303806             -0.051321   
Annualized Volatility                0.482320              0.501619   
Annualized Sharpe Ratio              0.559046             -0.170425   
Maximum Drawdown                    -0.682479             -0.635372   

                         Single - NVDA (BAH1)  Single - AAPL (BAH1)   
Measure                                                               
Cumulative Return                    3.698667              1.225956  \
Annualized Return                    0.626183              0.118053   
Annualized Volatility                0.498290              0.281590   
Annualized Sharpe Ratio              1.188095              0.297901   
Maximum Drawdown                    -0.531787             -0.309294   

                         Single - EWY (BAH1)  Single - DXJ (BAH2)   
Measure                                                             
Cumulative Return                   0.826615             1.668287  \
Annualized Return                  -0.043771             0.213159   
Annualized Volatility               0.243343             0.177744   
Annualized Sharpe Ratio            -0.320283             1.007016   
Maximum Drawdown                   -0.406293            -0.221939   

                         Single - BRK-B (BAH2)  Single - SPY (BAH1)   
Measure                                                               
Cumulative Return                     1.448369             1.160317  \
Annualized Return                     0.158196             0.073698   
Annualized Volatility                 0.175719             0.181010   
Annualized Sharpe Ratio               0.705835             0.218392   
Maximum Drawdown                     -0.265790            -0.244964   

                         Single - QQQ (BAH1)  
Measure                                       
Cumulative Return                   1.145235  
Annualized Return                   0.082118  
Annualized Volatility               0.244261  
Annualized Sharpe Ratio             0.196307  
Maximum Drawdown                   -0.348280

In [6]:
portfolio.get_position_for_trade()

2024-08-10 00:42:08,627 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - CRITICAL - Portfolio target capital is not specified, use initial backtest capital of $163,406
2024-08-10 00:42:08,628 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - INFO - Generate trade position based on target capital of $163,406


META  TSLA   NVDA   AAPL   EWY   DXJ  BRK-B   SPY   QQQ
Date                                                               
2022-01-03   0.0  44.0  795.0  267.0  11.0  77.0  116.0  42.0  12.0
2022-01-04   0.0  44.0  795.0  267.0  11.0  77.0  116.0  42.0  12.0
2022-01-05   0.0  44.0  795.0  267.0  11.0  77.0  116.0  42.0  12.0
2022-01-06   0.0  44.0  795.0  267.0  11.0  77.0  116.0  42.0  12.0
2022-01-07   0.0  44.0  795.0  267.0  11.0  77.0  116.0  42.0  12.0
...          ...   ...    ...    ...   ...   ...    ...   ...   ...
2024-08-05   1.0  29.0  231.0  203.0  36.0  69.0  103.0  36.0  14.0
2024-08-06   1.0  29.0  231.0  203.0  36.0  69.0  103.0  36.0  14.0
2024-08-07   1.0  29.0  231.0  203.0  36.0  69.0  103.0  36.0  14.0
2024-08-08   1.0  29.0  231.0  203.0  36.0  69.0  103.0  36.0  14.0
2024-08-09  37.0  50.0  104.0  176.0   0.0   0.0  116.0  41.0   4.0

[654 rows x 9 columns]

# Equal Weighted Portfolios

In [7]:
# portfolio = PortfolioStandard(    
#     capital=200000,
#     name='ETF Buy and Hold Portfolio',    
#     rebalance_iter=RebalancerIter('0 0 * * Fri', 2),
#     tc_model=TransactionCostFutu(),    
#     systems=[
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['META'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['TSLA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['NVDA'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         # TradingSubSystemSingle(vol_target=vol_target, instruments=['AAPL'],  strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['EWY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['DXJ'],   strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),        
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['VOE'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['VBR'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['BRK-B'], strategy=[BuyAndHoldStrategy(confidence=2)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['SPY'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),
#         TradingSubSystemSingle(vol_target=vol_target, instruments=['QQQ'],   strategy=[BuyAndHoldStrategy(confidence=1)], max_leverage=max_leverage),       
# ])

# portfolio.set_start_date(start_date)
# portfolio.set_end_date(end_date)
# portfolio.backtest_subsystems()
# portfolio.optimize()
# portfolio.backtest()
# portfolio.rebalance()
# portfolio.performance()

# Execute the Portfolio

In [8]:
executor = ExecutorFutu(is_test=False)
executor.set_portfolio(portfolio)
orders = executor.execute(px_interval='5m')
orders

2024-08-10 00:42:15,408 - ExecutorFutu - INFO - market: US
2024-08-10 00:42:15,409 - ExecutorFutu - INFO - Cancel all orders first before executing.....


2024-08-10 00:42:15,426 | 39753 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=1, host=127.0.0.1, port=11111, user_id=18214795
2024-08-10 00:42:15,583 | 39753 | [open_context_base.py] on_disconnect:383: Disconnected: conn_id=1


2024-08-10 00:42:18,588 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - CRITICAL - Portfolio target capital is not specified, use initial backtest capital of $163,406
2024-08-10 00:42:18,589 - Linear Optimized Portfolio (ETF Buy and Hold Portfolio) - INFO - Generate trade position based on target capital of $163,406
2024-08-10 00:42:18,596 - ExecutorFutu - INFO - Execute Linear Optimized Portfolio (ETF Buy and Hold Portfolio) position based on 2024-08-09


2024-08-10 00:42:18,600 | 39753 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=2, host=127.0.0.1, port=11111, user_id=18214795


2024-08-10 00:42:18,615 - Futu - INFO - 8 Positions: US.TSLA, US.SPY, US.QQQ, US.NVDA, US.EWY, US.DXJ, US.BRK.B, US.AAPL


...

2024-08-10 00:42:39,506 - Futu - INFO - Placed Order: {'code': 'US.BRK.B', 'price': 432.99, 'qty': 42.0, 'trd_side': 'BUY', 'order_type': 'NORMAL', 'market': 'US', 'trd_env': 'REAL'}


2024-08-10 00:42:39,509 | 39753 | [open_context_base.py] on_disconnect:383: Disconnected: conn_id=9
2024-08-10 00:42:42,524 | 39753 | [open_context_base.py] _send_init_connect_sync:311: InitConnect ok: conn_id=10, host=127.0.0.1, port=11111, user_id=18214795


2024-08-10 00:42:42,881 - Futu - INFO - Placed Order: {'code': 'US.SPY', 'price': 530.73, 'qty': 18.0, 'trd_side': 'BUY', 'order_type': 'NORMAL', 'market': 'US', 'trd_env': 'REAL'}


2024-08-10 00:42:42,883 | 39753 | [open_context_base.py] on_disconnect:383: Disconnected: conn_id=10


code            stock_name trd_side order_type order_status   
0   US.META        Meta Platforms      BUY     NORMAL   SUBMITTING  \
0   US.TSLA                   特斯拉     SELL     NORMAL   SUBMITTING   
0   US.NVDA                   英伟达     SELL     NORMAL   SUBMITTING   
0   US.AAPL                    苹果     SELL     NORMAL   SUBMITTING   
0    US.EWY    韩国ETF-iShares MSCI     SELL     NORMAL   SUBMITTING   
0    US.DXJ  日本对冲股票ETF-WisdomTree     SELL     NORMAL   SUBMITTING   
0  US.BRK.B                伯克希尔-B      BUY     NORMAL   SUBMITTING   
0    US.SPY       SPDR 标普500指数ETF      BUY     NORMAL   SUBMITTING   

              order_id    qty   price          create_time   
0  3916849729048727468   37.0  511.71  2024-08-09 12:42:19  \
0  5963508491051441716   52.0  197.83  2024-08-09 12:42:22   
0  1092756237091749970  187.0  104.51  2024-08-09 12:42:26   
0  5580336386812993045   55.0  214.79  2024-08-09 12:42:29   
0    81773934495081067   90.0   62.00  2024-08-09 12:42:32   
0  2090149019262207478   46.0   96.83  2024-08-09 12:42:35   
0  2522696133180476418   42.0  432.99  2024-08-09 12:42:39   
0  1013166903146742157   18.0  530.73  2024-08-09 12:42:42   

          updated_time  ...   
0  2024-08-09 12:42:19  ...  \
0  2024-08-09 12:42:22  ...   
0  2024-08-09 12:42:26  ...   
0  2024-08-09 12:42:29  ...   
0  2024-08-09 12:42:32  ...   
0  2024-08-09 12:42:35  ...   
0  2024-08-09 12:42:39  ...   
0  2024-08-09 12:42:42  ...   

                                              remark  time_in_force   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY  \
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   
0  Linear Optimized Portfolio (ETF Buy and Hold P...            DAY   

  fill_outside_rth aux_price trail_type  trail_value trail_spread currency   
0            False       N/A        N/A          N/A          N/A      USD  \
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   
0            False       N/A        N/A          N/A          N/A      USD   

                                           portfolio       date  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-09  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-09  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-09  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-09  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-09  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-09  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-09  
0  Linear Optimized Portfolio (ETF Buy and Hold P... 2024-08-09  

[8 rows x 23 columns]